In [ ]:
pip install albumentations

#여러 개의 이미지 증강 처리

In [ ]:
import albumentations as A
from albumentations.pytorch import ToTensorV2
import cv2
import torch
import numpy as np
import os

# GPU 사용 가능 여부 확인
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# 이미지 로드 함수
def load_image(image_path):
    try:
        image = cv2.imread(image_path)
        if image is None:
            raise FileNotFoundError(f"이미지를 로드할 수 없습니다: {image_path}")
        image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        return image
    except Exception as e:
        print(f"이미지 로드 오류 ({image_path}): {e}")
        return np.zeros((300, 300, 3), dtype=np.uint8)

# 다양한 증강 파이프라인 정의 (size 매개변수 수정)
transforms = [
    # 1. 회전
    A.Compose([
        A.Resize(224, 224),  # height, width 대신 직접 값 전달
        A.Rotate(limit=45, p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        ToTensorV2()
    ]),
    # 2. 좌우 반전 + 밝기/대비 조정
    A.Compose([
        A.Resize(224, 224),
        A.HorizontalFlip(p=1.0),
        A.RandomBrightnessContrast(p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        ToTensorV2()
    ]),
    # 3. 색상 조정
    A.Compose([
        A.Resize(224, 224),
        A.ColorJitter(p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        ToTensorV2()
    ]),
    # 4. 자르기 + 회전
    A.Compose([
        A.SmallestMaxSize(max_size=224),  # 가장 작은 면을 224로 리사이즈
        A.CenterCrop(height=224, width=224),  # 그 다음 중앙 자르기
        A.Rotate(limit=30, p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        ToTensorV2()
    ]),
    # 5. 선명도 조정
    A.Compose([
        A.Resize(224, 224),
        A.Sharpen(p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        ToTensorV2()
    ]),
    
    # 6. 블러 효과
    A.Compose([
        A.Resize(height=224, width=224),
        A.Blur(blur_limit=7, p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        ToTensorV2()
    ]),
    
    # 7. 색상 변환(1)
    A.Compose([
        A.Resize(224, 224),
        A.OneOf([
            A.ColorJitter(brightness=0.5, contrast=0.5, saturation=0.5, hue=0.5, p=1.0),
            A.RandomBrightnessContrast(brightness_limit=0.7, contrast_limit=0.7, p=1.0),
        ], p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        A.ToTensorV2()
    ]),

    # 8. 색상 변환(2)
    A.Compose([
        A.Resize(224, 224),
        A.OneOf([
            A.HueSaturationValue(hue_shift_limit=40, sat_shift_limit=60, val_shift_limit=40, p=1.0),
            A.RGBShift(r_shift_limit=40, g_shift_limit=40, b_shift_limit=40, p=1.0),
        ], p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        A.ToTensorV2()
    ]),
    
    # 9. 노이즈 추가(1)
    A.Compose([
        A.Resize(224, 224),
        A.GaussNoise(std_range=(0.2, 0.6), p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        A.ToTensorV2()
    ]),

    # 10. 노이즈 추가(2)
    A.Compose([
        A.Resize(224, 224),
        A.ISONoise(color_shift=(0.01, 0.05), intensity=(0.1, 0.5), p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        A.ToTensorV2()
    ]),

    # 11. 노이즈 추가(3)
    A.Compose([
        A.Resize(224, 224),
        A.MultiplicativeNoise(multiplier=(0.9, 1.1), per_channel=True, p=1.0),
        A.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
        A.ToTensorV2()
    ])
]

#여러 방식의 증강 방식 처리
def augment_multiple(image, num_augmentations=10):
    augmented_images = []
    
    for i in range(num_augmentations):
        try:
            img_array = np.array(image).astype(np.uint8)
            augmented = transforms[i](image=img_array)
            augmented_image = augmented['image']
            augmented_images.append(augmented_image)
        except Exception as e:
            print(f"이미지 증강 중 오류 발생 (증강 {i+1}): {e}")
            continue
    
    return augmented_images

def process_images(image_folder, output_folder):
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    image_files = [f for f in os.listdir(image_folder) if f.lower().endswith(('.png', '.jpg', '.jpeg'))]
    
    for idx, image_file in enumerate(image_files):
        image_path = os.path.join(image_folder, image_file)
        image = load_image(image_path)
        
        try:
            augmented_images = augment_multiple(image)
            if augmented_images:
                for i, aug_image in enumerate(augmented_images):
                    # 시각화를 위한 변환
                    denorm_image = aug_image.permute(1, 2, 0).cpu().numpy()
                    denorm_image = (denorm_image * [0.229, 0.224, 0.225] + [0.485, 0.456, 0.406]) * 255.0
                    denorm_image = np.clip(denorm_image, 0, 255).astype(np.uint8)
                    
                    # 이미지 저장
                    output_path = os.path.join(output_folder, f'{os.path.splitext(image_file)[0]}_aug_{i+1}.png')
                    cv2.imwrite(output_path, cv2.cvtColor(denorm_image, cv2.COLOR_RGB2BGR))
                
                print(f"이미지 {idx+1}/{len(image_files)} 처리 완료: {image_file}")
            else:
                print(f"이미지 {idx+1}/{len(image_files)} 증강 실패: {image_file}")
        except Exception as e:
            print(f"이미지 {idx+1}/{len(image_files)} 처리 중 오류 발생 ({image_file}): {e}")

if __name__ == "__main__":
    input_folder = "Input"  # 입력 이미지가 있는 폴더
    output_folder = "Output"  # 증강된 이미지를 저장할 폴더
    
    process_images(input_folder, output_folder)
    
    print("모든 이미지 처리가 완료되었습니다.")


이미지 1/2631 처리 완료: IN_H00286_SN1_090402_28709.png
이미지 2/2631 처리 완료: IN_H00286_SN1_090402_28712.png
이미지 3/2631 처리 완료: IN_H00286_SN1_090402_28715.png
이미지 4/2631 처리 완료: IN_H00286_SN1_090402_28718.png
이미지 5/2631 처리 완료: IN_H00286_SN1_090402_28721.png
이미지 6/2631 처리 완료: IN_H00286_SN1_090402_28724.png
이미지 7/2631 처리 완료: IN_H00286_SN1_090402_28727.png
이미지 8/2631 처리 완료: IN_H00286_SN1_090402_28730.png
이미지 9/2631 처리 완료: IN_H00286_SN1_090402_28733.png
이미지 10/2631 처리 완료: IN_H00286_SN1_090402_28736.png
이미지 11/2631 처리 완료: IN_H00286_SN1_090402_28739.png
이미지 12/2631 처리 완료: IN_H00286_SN1_090402_28742.png
이미지 13/2631 처리 완료: IN_H00286_SN1_090402_28745.png
이미지 14/2631 처리 완료: IN_H00286_SN1_090402_28748.png
이미지 15/2631 처리 완료: IN_H00286_SN1_090402_28751.png
이미지 16/2631 처리 완료: IN_H00286_SN1_090402_28754.png
이미지 17/2631 처리 완료: IN_H00286_SN1_090402_28757.png
이미지 18/2631 처리 완료: IN_H00286_SN1_090402_28760.png
이미지 19/2631 처리 완료: IN_H00286_SN1_090402_28763.png
이미지 20/2631 처리 완료: IN_H00286_SN1_090402_28766.png
이미지 21/26

#증강한 이미지의 XML 라벨 파일 확보보

In [ ]:
import os
import shutil
import re

#원본 이미지에서 파일 이름 추출출
def extract_original_filename(filename):
    match = re.search(r'(.+?)_aug_', filename)
    if match:
        return match.group(1)
    else:
        return filename

def process_images(input_folder, label_folder, output_folder):
    print("프로세스 시작...")

    # 출력 폴더가 없으면 생성
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)
        print(f"출력 폴더 생성됨: {output_folder}")
    else:
        print(f"출력 폴더 이미 존재함: {output_folder}")

    # 입력 폴더의 모든 이미지 파일 처리
    for image_filename in os.listdir(input_folder):
        if image_filename.endswith(('.png', '.jpg', '.jpeg')):  # 이미지 파일 확장자 확인
            print(f"\n이미지 파일 처리 중: {image_filename}")
            
            original_filename = extract_original_filename(image_filename)
            print(f"추출된 원본 파일명: {original_filename}")

            # XML 파일 찾기
            xml_filename = f"{original_filename}.xml"
            xml_path = os.path.join(label_folder, xml_filename)
            
            if os.path.exists(xml_path):
                # XML 파일 복사 (.png 확장자 제거)
                output_filename = os.path.splitext(image_filename)[0] + '.xml'
                dst = os.path.join(output_folder, output_filename)
                shutil.copy2(xml_path, dst)
                print(f"XML 파일 복사 완료: {xml_path} -> {dst}")
            else:
                print(f"경고: XML 파일을 찾을 수 없음: {xml_filename}")

    print("\n모든 처리 완료.")

# 사용 예시
input_folder = "C:/Users/USER/Desktop/Local/Output" #증강된 이미지가 들어있는 폴더
label_folder = "C:/Users/USER/Desktop/Giiit/FootTrafficReport/people-detection/PAR/dataset/Label" #원본 라벨이 담긴 폴더
output_folder = "C:/Users/USER/Desktop/Local/Output_Label" #증강된 이미지 이름과 동일한 xml 파일이 생성된 폴더

print("프로그램 시작")
print(f"입력 폴더 (이미지): {input_folder}")
print(f"라벨 폴더 (XML): {label_folder}")
print(f"출력 폴더: {output_folder}")

process_images(input_folder, label_folder, output_folder)
print("프로그램 종료")


프로그램 시작
입력 폴더 (이미지): C:/Users/USER/Desktop/Local/Output
라벨 폴더 (XML): C:/Users/USER/Desktop/Giiit/FootTrafficReport/people-detection/PAR/dataset/Label
출력 폴더: C:/Users/USER/Desktop/Local/Output_Label
프로세스 시작...
출력 폴더 이미 존재함: C:/Users/USER/Desktop/Local/Output_Label

이미지 파일 처리 중: IN_H00286_SN1_090402_28709_aug_1.png
추출된 원본 파일명: IN_H00286_SN1_090402_28709
XML 파일 복사 완료: C:/Users/USER/Desktop/Giiit/FootTrafficReport/people-detection/PAR/dataset/Label\IN_H00286_SN1_090402_28709.xml -> C:/Users/USER/Desktop/Local/Output_Label\IN_H00286_SN1_090402_28709_aug_1.xml

이미지 파일 처리 중: IN_H00286_SN1_090402_28709_aug_10.png
추출된 원본 파일명: IN_H00286_SN1_090402_28709
XML 파일 복사 완료: C:/Users/USER/Desktop/Giiit/FootTrafficReport/people-detection/PAR/dataset/Label\IN_H00286_SN1_090402_28709.xml -> C:/Users/USER/Desktop/Local/Output_Label\IN_H00286_SN1_090402_28709_aug_10.xml

이미지 파일 처리 중: IN_H00286_SN1_090402_28709_aug_2.png
추출된 원본 파일명: IN_H00286_SN1_090402_28709
XML 파일 복사 완료: C:/Users/USER/Desktop/Giiit/FootTraf

#XML 파일 이름과 내부 name 태그 일치

In [ ]:
import os
import xml.etree.ElementTree as ET

# 경로 설정
label_path = "Output_Label"

# XML 파일 이름과 내부 FILE/name 태그를 일치시키는 코드
for xml_file in os.listdir(label_path):
    if xml_file.endswith(".xml"):
        # XML 파일 경로
        xml_file_path = os.path.join(label_path, xml_file)
        
        # XML 파싱
        tree = ET.parse(xml_file_path)
        root = tree.getroot()
        
        # XML 파일 이름에서 확장자를 제외한 이름 가져오기
        xml_base_name = xml_file[:-4]
        
        # FILE/name 태그의 현재 값 가져오기
        file_name_tag = root.find("FILE/name")
        current_name = file_name_tag.text
        
        # 현재 이름이 aug가 포함되지 않았고, XML 파일명에 aug가 포함된 경우
        if '_aug_' not in current_name and '_aug_' in xml_base_name:
            # 새로운 파일명 생성 (.png 확장자 포함)
            new_file_name = xml_base_name + '.png'
            
            # FILE/name 태그 업데이트
            file_name_tag.text = new_file_name
            
            # 변경된 XML 저장
            tree.write(xml_file_path)
            print(f"Updated: {current_name} -> {new_file_name}")
